In [1]:
import pandas as pd
import numpy as np
import time
import random

# -*- coding: utf-8 -*-
from bs4 import BeautifulSoup
import requests
import re
from datetime import date
# remember to install the library: pip install scraperapi-sdk
from scraper_api import ScraperAPIClient

# for parallelization
from joblib import Parallel, delayed
import multiprocessing
from multiprocessing import Manager

headers = {'User-Agent':'Mozilla/5.0 (X11; Linux x86_64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/86.0.4240.183',#Safari/537.36
'Accept-Encoding': 'identity'
}


#'Accept-Encoding': 'identity'
#url = 'https://www.realtor.com/realestateandhomes-search/Atlanta_GA/pg-0'
#response=requests.get(url,headers=headers)

In [2]:
client = ScraperAPIClient('c72673098a63fab1bc69b67253f7c93b') #my gmail
#client = ScraperAPIClient('a27221db7e9a27526f076a1fdc66dc51') #hotmail
#county_lst = ["Cook-County_IL"]#,"DeKalb-County_GA","Fulton-County_GA", "Cobb-County_GA", "Gwinnett-County_GA", "Henry-County_GA", "Douglas-County_GA"]
city_lst = ["Chicago_IL"]

## Scraping Rentals

In [3]:
# this will be the new code. Needs validation that the listing coming out are cohesive. 
# It may make sense to add the listing link to the df so that can easily do a sanity check on the listing info

# also note that I realize using regex is janky. chatgpt wanted to use json to parse the listing info,
# but it seems the structure was so bad that json.loads never worked.

idx=0
prop_df = pd.DataFrame()
listings = []
#for county in county_lst:
for city in city_lst:
    
    """ Need to find out how many pages of results came back for each county search so can know how many to loop
    through. Find this info on the first page of results"""
    
    #url = 'https://www.realtor.com/apartments/' + county +'/pg-'
    url = 'https://www.realtor.com/apartments/' + city +'/pg-'
    
    realtor_url1 = url + str(0)
    
    #using scraper api instead of requests library
    response = client.get(url = realtor_url1)
    print(city)
    print(response)

    myr2 = response.text
    
    #this bit will work for getting listings count for apartments
    lstings_a = re.search('See all (.+apartments)', myr2)
    lstings_a = int(lstings_a.group(1).split(" ")[0].strip())
 
    ##couldn't find number of pages on the apartments search. So get the number of listings and assume 41 listings 
    #per page in order to figure out how many pages to loop through
    pages_of_results = round(lstings_a / 41)
    #pages_of_results = 2
    
    n_pages = 0
    
    for page in list(range(0, pages_of_results)):

        """Use the scaperapiclient to get requests from webpages using a different proxy for each page.
        Convert the content to soup, isolate the chunk of html we need and convert to string.
        Pull the info we need for each property from the string and put it into a list of dictionaries. 
        then can convert to dataframe
        .group() returns the part of the string where there was a match
        """
        print('page: ' + str(page))
        n_pages += 1
        realtor_url = url + "0" + str(page)
        print(realtor_url)

        response = client.get(url = realtor_url)
        print(response )

        #response=requests.get(realtor_url,headers=headers)

        soup = BeautifulSoup(response.content,'html.parser')

        #get the chunk of html that contains th info we want
        #and convert it to a string
        json_data = str(soup.find_all(id='__NEXT_DATA__')).split("props")[1]
        json_data = '{"props' + json_data

        #print(json_data)
        print("************************************")
        
        #This will give us the chunk of text with some of the listings info, to pull all the listing on a page
        r3 = json_data

        #get the indexes for property id and permalink so can know where to break up string for individual properties
        start_idx = [idx.start() for idx in re.finditer('property_id', r3)]
        end_idx = [idx.start() for idx in re.finditer('products":', r3)]

        
        for i in range(0, len(start_idx)-1):
            try:

                #loop through the text of html on a page and pull out the slices that correspond to a particular property.
                # don't use the end index, it throws everything off. Also search will just find the first match so it's fine.
                # search returns a match object
                r4 = r3[start_idx[i] : ]#end_idx[i]]

                listing_id = re.search('listing_id":(.+?),', r4)
                property_id = re.search('property_id":(.+?),', r4)
                prop_type = re.search('prop_type":(.+?),', r4)
                lat= re.search('lat":(.+?),', r4)    
                lon = re.search('lon":(.+?)}', r4)    
                address = re.search('line":(.+?),', r4)
                price = re.search('list_price":(.+?),', r4)
                price_max = re.search('list_price_max":(.+?),', r4)
                price_min = re.search('list_price_min":(.+?),', r4)
                permalink = re.search('permalink":(.+?),', r4)
                description = re.search('"description":(.*?)}', r4)
                """
                print(listing_id)
                print(address)
                print(price_max)
                print(permalink)
                print(description)
                """

                # create a list of dictionaries to store the info

                dic = {'property_id': property_id.group(1).replace('"',''),
                        'listing_id' : listing_id.group(1).replace('"',''), 
                        'prop_type' : prop_type.group(1).replace('"',''), 
                        'latitude': lat.group(1), 
                        'longitude': lon.group(1), 
                        'address': address.group(1).replace('"',''),
                        'price': price.group(1).replace('"',''),
                        'price_max' : price_max.group(1).replace('"',''),
                        'price_min' : price_max.group(1).replace('"',''),
                        'link' : 'https://www.realtor.com/realestateandhomes-detail/' + permalink.group(1).replace('"',''),
                        'description' : description.group(1).replace('"',' '),
                       }
                print(dic)
                print("********************")
                listings.append(dic)

            except:
                print("some exception for ", i)
                print("********************")


Chicago_IL
<Response [200]>
page: 0
https://www.realtor.com/apartments/Chicago_IL/pg-00
<Response [200]>
************************************
{'property_id': '7012743122', 'listing_id': '2949506125', 'prop_type': '[{type:home', 'latitude': '41.754746', 'longitude': '-87.552012', 'address': '7800 S SOUTH SHORE DR', 'price': 'null', 'price_max': '955', 'price_min': '955', 'link': 'https://www.realtor.com/realestateandhomes-detail/7800-S-South-Shore-Dr_Chicago_IL_60649_M70127-43122', 'description': '{ beds :null, beds_max :1, beds_min :1, baths_min :1, baths_max :1, baths_consolidated :null, garage :null, garage_min :null, garage_max :null, sqft :null, sqft_max :605, sqft_min :605, name : 7800 S South Shore Dr , sub_type :null, type : apartment , year_built :null'}
********************
{'property_id': '7783154884', 'listing_id': '2953713665', 'prop_type': '[{type:home', 'latitude': '41.482088', 'longitude': '-87.675665', 'address': '3324 Western Ave', 'price': 'null', 'price_max': '1400',

<Response [200]>
************************************
{'property_id': '7012743122', 'listing_id': '2949506125', 'prop_type': '[{type:home', 'latitude': '41.754746', 'longitude': '-87.552012', 'address': '7800 S SOUTH SHORE DR', 'price': 'null', 'price_max': '955', 'price_min': '955', 'link': 'https://www.realtor.com/realestateandhomes-detail/7800-S-South-Shore-Dr_Chicago_IL_60649_M70127-43122', 'description': '{ beds :null, beds_max :1, beds_min :1, baths_min :1, baths_max :1, baths_consolidated :null, garage :null, garage_min :null, garage_max :null, sqft :null, sqft_max :605, sqft_min :605, name : 7800 S South Shore Dr , sub_type :null, type : apartment , year_built :null'}
********************
{'property_id': '7783154884', 'listing_id': '2953713665', 'prop_type': '[{type:home', 'latitude': '41.482088', 'longitude': '-87.675665', 'address': '3324 Western Ave', 'price': 'null', 'price_max': '1400', 'price_min': '1400', 'link': 'https://www.realtor.com/realestateandhomes-detail/3324-We

<Response [200]>
************************************
{'property_id': '7045929928', 'listing_id': '2949505998', 'prop_type': '[{type:home', 'latitude': '41.704661', 'longitude': '-87.612125', 'address': '10425 S VERNON AVE', 'price': 'null', 'price_max': '970', 'price_min': '970', 'link': 'https://www.realtor.com/realestateandhomes-detail/10425-S-Vernon-Ave_Chicago_IL_60628_M70459-29928', 'description': '{ beds :null, beds_max :2, beds_min :1, baths_min :1, baths_max :1, baths_consolidated :null, garage :null, garage_min :null, garage_max :null, sqft :null, sqft_max :650, sqft_min :615, name : 10425 S Vernon , sub_type :null, type : apartment , year_built :null'}
********************
{'property_id': '8537174736', 'listing_id': '2949505880', 'prop_type': '[{type:home', 'latitude': '41.901018', 'longitude': '-87.751717', 'address': '1117 N LAWLER AVE', 'price': 'null', 'price_max': '1265', 'price_min': '1265', 'link': 'https://www.realtor.com/realestateandhomes-detail/1117-N-Lawler-Ave_C

<Response [200]>
************************************
{'property_id': '8258124330', 'listing_id': '2949506154', 'prop_type': '[{type:home', 'latitude': '41.744595', 'longitude': '-87.604126', 'address': '8236 S MARYLAND AVE', 'price': 'null', 'price_max': '905', 'price_min': '905', 'link': 'https://www.realtor.com/realestateandhomes-detail/8236-S-Maryland-Ave_Chicago_IL_60619_M82581-24330', 'description': '{ beds :null, beds_max :2, beds_min :1, baths_min :1, baths_max :1, baths_consolidated :null, garage :null, garage_min :null, garage_max :null, sqft :null, sqft_max :850, sqft_min :650, name : 8236 S Maryland , sub_type :null, type : apartment , year_built :null'}
********************
{'property_id': '8921031153', 'listing_id': '2949506021', 'prop_type': '[{type:home', 'latitude': '41.76596', 'longitude': '-87.569808', 'address': '2235 E 71ST ST', 'price': 'null', 'price_max': '710', 'price_min': '710', 'link': 'https://www.realtor.com/realestateandhomes-detail/2235-E-71st-St_Chicago

<Response [200]>
************************************
{'property_id': '7305950609', 'listing_id': '2953722071', 'prop_type': '[{type:home', 'latitude': '41.747993', 'longitude': '-87.56424', 'address': '8100-8114 S Essex Ave', 'price': 'null', 'price_max': '970', 'price_min': '970', 'link': 'https://www.realtor.com/realestateandhomes-detail/8100-S-Essex-Ave_Chicago_IL_60617_M73059-50609', 'description': '{ beds :null, beds_max :3, beds_min :0, baths_min :1, baths_max :1, baths_consolidated :null, garage :null, garage_min :null, garage_max :null, sqft :null, sqft_max :975, sqft_min :525, name : 8100 S Essex Ave , sub_type :null, type : apartment , year_built :null'}
********************
{'property_id': '7258568386', 'listing_id': '2949505860', 'prop_type': '[{type:home', 'latitude': '41.874668', 'longitude': '-87.755127', 'address': '400 S LARAMIE AVE', 'price': 'null', 'price_max': '1115', 'price_min': '1115', 'link': 'https://www.realtor.com/realestateandhomes-detail/400-S-Laramie-Ave

...

<Response [200]>
************************************
{'property_id': '9398212736', 'listing_id': '2956719581', 'prop_type': '[{type:home', 'latitude': '41.9587499', 'longitude': '-87.6650368', 'address': '1415 W Hutchinson St Unit 4218-2', 'price': '1895', 'price_max': 'null', 'price_min': 'null', 'link': 'https://www.realtor.com/realestateandhomes-detail/1415-W-Hutchinson-St-4218-2_Chicago_IL_60613_M93982-12736', 'description': '{ beds :1, beds_max :null, beds_min :null, baths_min :null, baths_max :null, baths_consolidated : 1 , garage :null, garage_min :null, garage_max :null, sqft :null, sqft_max :null, sqft_min :null, name :null, sub_type : condo , type : apartment , year_built :null'}
********************
{'property_id': '9385672541', 'listing_id': '2954716388', 'prop_type': '[{type:home', 'latitude': '41.968243', 'longitude': '-87.67488', 'address': '4746 N Ravenswood Ave Unit W330', 'price': '2115', 'price_max': 'null', 'price_min': 'null', 'link': 'https://www.realtor.com/real

<Response [200]>
************************************
{'property_id': '9147011761', 'listing_id': '2961951718', 'prop_type': '[{type:home', 'latitude': '41.894478', 'longitude': '-87.639763', 'address': '433 W Huron St Unit 1307', 'price': '2712', 'price_max': 'null', 'price_min': 'null', 'link': 'https://www.realtor.com/realestateandhomes-detail/433-W-Huron-St-707_Chicago_IL_60654_M91470-11761', 'description': '{ beds :1, beds_max :null, beds_min :null, baths_min :null, baths_max :null, baths_consolidated : 1 , garage :null, garage_min :null, garage_max :null, sqft :770, sqft_max :null, sqft_min :null, name :null, sub_type : condo , type : apartment , year_built :null'}
********************
{'property_id': '9091869809', 'listing_id': '2956634871', 'prop_type': '[{type:home', 'latitude': '41.9704124', 'longitude': '-87.6800802', 'address': '2015 W Ainslie St Unit 2019-2', 'price': '1995', 'price_max': 'null', 'price_min': 'null', 'link': 'https://www.realtor.com/realestateandhomes-deta

<Response [404]>
************************************
page: 208
https://www.realtor.com/apartments/Chicago_IL/pg-0208
<Response [404]>
************************************
page: 209
https://www.realtor.com/apartments/Chicago_IL/pg-0209
<Response [404]>
************************************
page: 210
https://www.realtor.com/apartments/Chicago_IL/pg-0210
<Response [404]>
************************************
page: 211
https://www.realtor.com/apartments/Chicago_IL/pg-0211
<Response [404]>
************************************
page: 212
https://www.realtor.com/apartments/Chicago_IL/pg-0212
<Response [404]>
************************************
page: 213
https://www.realtor.com/apartments/Chicago_IL/pg-0213
<Response [404]>
************************************
page: 214
https://www.realtor.com/apartments/Chicago_IL/pg-0214
<Response [404]>
************************************
page: 215
https://www.realtor.com/apartments/Chicago_IL/pg-0215
<Response [404]>
************************************
pa

<Response [404]>
************************************
page: 278
https://www.realtor.com/apartments/Chicago_IL/pg-0278
<Response [404]>
************************************
page: 279
https://www.realtor.com/apartments/Chicago_IL/pg-0279
<Response [404]>
************************************
page: 280
https://www.realtor.com/apartments/Chicago_IL/pg-0280
<Response [404]>
************************************
page: 281
https://www.realtor.com/apartments/Chicago_IL/pg-0281
<Response [404]>
************************************
page: 282
https://www.realtor.com/apartments/Chicago_IL/pg-0282
<Response [404]>
************************************
page: 283
https://www.realtor.com/apartments/Chicago_IL/pg-0283
<Response [404]>
************************************
page: 284
https://www.realtor.com/apartments/Chicago_IL/pg-0284
<Response [404]>
************************************
page: 285
https://www.realtor.com/apartments/Chicago_IL/pg-0285
<Response [404]>
************************************
pa

<Response [404]>
************************************
page: 348
https://www.realtor.com/apartments/Chicago_IL/pg-0348
<Response [404]>
************************************
page: 349
https://www.realtor.com/apartments/Chicago_IL/pg-0349
<Response [404]>
************************************
page: 350
https://www.realtor.com/apartments/Chicago_IL/pg-0350
<Response [404]>
************************************
page: 351
https://www.realtor.com/apartments/Chicago_IL/pg-0351
<Response [404]>
************************************
page: 352
https://www.realtor.com/apartments/Chicago_IL/pg-0352
<Response [404]>
************************************
page: 353
https://www.realtor.com/apartments/Chicago_IL/pg-0353
<Response [404]>
************************************
page: 354
https://www.realtor.com/apartments/Chicago_IL/pg-0354
<Response [404]>
************************************
page: 355
https://www.realtor.com/apartments/Chicago_IL/pg-0355
<Response [404]>
************************************
pa

In [4]:
df = pd.DataFrame(listings)
df

property_id  listing_id    prop_type   latitude   longitude  \
0     7012743122  2949506125  [{type:home  41.754746  -87.552012   
1     7783154884  2953713665  [{type:home  41.482088  -87.675665   
2     9603357820  2956787949  [{type:home  41.897031   -87.63454   
3     8228833300  2949505820  [{type:home  41.764516  -87.582066   
4     7800131002  2949505951  [{type:home   41.75333  -87.562607   
...          ...         ...          ...        ...         ...   
8689  8437336186  2956091352  [{type:home  41.896639  -87.671849   
8690  8344599846  2943609613  [{type:home  41.885431   -87.61532   
8691  8329885695  2946509397  [{type:home  42.018767  -87.692346   
8692  8353908687  2955660177  [{type:home   41.93157  -87.649319   
8693  8326665234  2958990615  [{type:home  41.804115  -87.617096   

                        address price price_max price_min  \
0         7800 S SOUTH SHORE DR  null       955       955   
1              3324 Western Ave  null      1400      1400   
2                808 N Wells St  null      4234      4234   
3                1734 E 72nd St  null       930       930   
4           7801 S KINGSTON AVE  null       945       945   
...                         ...   ...       ...       ...   
8689        819 N Wood St Apt 1  3400      null      null   
8690   175 N Harbor Dr Apt 2415  2450      null      null   
8691   2451 W Howard St Apt 406  2200      null      null   
8692  2700 N Halsted St Apt 412  2775      null      null   
8693      4956 S King Dr Unit 2  2135      null      null   

                                                   link  \
0     https://www.realtor.com/realestateandhomes-det...   
1     https://www.realtor.com/realestateandhomes-det...   
2     https://www.realtor.com/realestateandhomes-det...   
3     https://www.realtor.com/realestateandhomes-det...   
4     https://www.realtor.com/realestateandhomes-det...   
...                                                 ...   
8689  https://www.realtor.com/realestateandhomes-det...   
8690  https://www.realtor.com/realestateandhomes-det...   
8691  https://www.realtor.com/realestateandhomes-det...   
8692  https://www.realtor.com/realestateandhomes-det...   
8693  https://www.realtor.com/realestateandhomes-det...   

                                            description  
0     { beds :null, beds_max :1, beds_min :1, baths_...  
1     { beds :null, beds_max :3, beds_min :1, baths_...  
2     { beds :null, beds_max :2, beds_min :0, baths_...  
3     { beds :null, beds_max :3, beds_min :0, baths_...  
4     { beds :null, beds_max :2, beds_min :2, baths_...  
...                                                 ...  
8689  { beds :4, beds_max :null, beds_min :null, bat...  
8690  { beds :1, beds_max :null, beds_min :null, bat...  
8691  { beds :2, beds_max :null, beds_min :null, bat...  
8692  { beds :1, beds_max :null, beds_min :null, bat...  
8693  { beds :2, beds_max :null, beds_min :null, bat...  

[8694 rows x 11 columns]

In [5]:
#df.to_csv("Chicago_Rentals_Sample_Oct1923.csv")
df.to_csv("Chicago_Rentals_Sample_Dec2823.csv")

In [6]:
len(df.drop_duplicates())

6559

In [7]:
pages_of_results

365

In [ ]:
# drop rows that don't have a property id
prop_df = prop_df[prop_df["property_id"].notna()].reset_index(drop=True)

## Reference

In [ ]:
"""# code for working with a single page of listings

#This will give us the chunk of text with some of the listings info, to pull all the listing on a page
r3 = json_data

#get the indexes for property id and permalink so can know where to break up string for individual properties
start_idx = [idx.start() for idx in re.finditer('property_id', r3)]
end_idx = [idx.start() for idx in re.finditer('products":', r3)]

listings = []
for i in range(0, len(start_idx)-1):
    try:

        #loop through the text of html on a page and pull out the slices that correspond to a particular property.
        # don't use the end index, it throws everything off. Also search will just find the first match so it's fine.
        # search returns a match object
        r4 = r3[start_idx[i] : ]#end_idx[i]]

        listing_id = re.search('listing_id":(.+?),', r4)
        property_id = re.search('property_id":(.+?),', r4)
        prop_type = re.search('prop_type":(.+?),', r4)
        lat= re.search('lat":(.+?),', r4)    
        lon = re.search('lon":(.+?)}', r4)    
        address = re.search('line":(.+?),', r4)
        price = re.search('list_price":(.+?),', r4)
        price_max = re.search('list_price_max":(.+?),', r4)
        price_min = re.search('list_price_min":(.+?),', r4)
        permalink = re.search('permalink":(.+?),', r4)
        description = re.search('"description":(.*?)}', r4)
        """
        print(listing_id)
        print(address)
        print(price_max)
        print(permalink)
        print(description)
        """
        
        # create a list of dictionaries to store the info
        
        dic = {'property_id': property_id.group(1).replace('"',''),
                'listing_id' : listing_id.group(1).replace('"',''), 
                'prop_type' : prop_type.group(1).replace('"',''), 
                'latitude': lat.group(1), 
                'longitude': lon.group(1), 
                'address': address.group(1).replace('"',''),
                'price': price.group(1).replace('"',''),
                'price_max' : price_max.group(1).replace('"',''),
                'price_min' : price_max.group(1).replace('"',''),
                'link' : 'https://www.realtor.com/realestateandhomes-detail/' + permalink.group(1).replace('"',''),
                'description' : description.group(1).replace('"',' '),
               }
        print(dic)
        print("********************")
        listings.append(dic)
        
    except:
        print("some exception for ", i)
        print("********************")
        """